In [1]:
import tarfile

import tqdm
import xarray as xr
import hvplot.xarray

import radolan_to_netcdf as rtn

# Download RADKLIM-YW data for May 2016

We want to look at the data for the flooding in the city of Braunsbach on 29th of May 2016.

**Note that RADKLIM data is corrected based on long-term statistics. Hence, these correction are not adjusted for individual events, like the one shown here. Like all radar rainfall estimate, and all rainfall estimates in general, the absolute values have to be treated with caution. The data is shown here only to highlight how easy it now is to access and explore RADOLAN and RADKLIM data.**

In [2]:
!curl -O https://opendata.dwd.de/climate_environment/CDC/grids_germany/5_minutes/radolan/reproc/2017_002/bin/2016/YW2017.002_201605.tar

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  393M  100  393M    0     0  3412k      0  0:01:57  0:01:57 --:--:-- 3524k0  0:02:06  0:00:29  0:01:37 2918k:00:31  0:01:34 3088k6  0:01:18 3446k2:02  0:01:17  0:00:45 3116k     0  0:02:04  0:01:35  0:00:29 3107k40k      0  0:02:00  0:01:44  0:00:16 4723k


# Read data from nested tar file

Data is provided as monthly tar files, which contains dailt tar.gz files, which contain the 5-minute binary files. To avoid extracting everything first we use the nested loop-construct below and extract only the data we want on the fly.

In [3]:
fn_netcdf = 'radklim-yw.nc'
rtn.create_empty_netcdf(fn=fn_netcdf, product_name='YW')

with tarfile.open('YW2017.002_201605.tar', 'r') as tar:
    fn_list = tar.getnames()
    fn_list.sort()
    for fn in fn_list[28:29]:
        print(f'Extracting daily file {fn}')
        f = tar.extractfile(fn)
        with tarfile.open(fileobj=f) as tar_inner:
            fn_list_inner = tar_inner.getnames()
            fn_list_inner.sort()
            # We only extract the 5-minute data from the afternoon
            for fn_inner in tqdm.tqdm(fn_list_inner[-120:-60]):
                #print(f'parsing {fn_inner}')
                data, metadata = rtn.read_in_one_bin_file(tar_inner.extractfile(fn_inner))
                rtn.append_to_netcdf(
                    fn_netcdf, 
                    data_list=[data, ], 
                    metadata_list=[metadata, ],
                )

Extracting daily file YW2017.002_20160529.tar.gz


100%|██████████| 60/60 [00:40<00:00,  1.48it/s]


In [4]:
ds = xr.open_dataset('radklim-yw.nc')
ds

<xarray.Dataset>
Dimensions:          (time: 60, x: 900, y: 1100)
Coordinates:
  * x                (x) float64 -443.5 -442.5 -441.5 ... 453.5 454.5 455.5
  * y                (y) float64 -4.759e+03 -4.758e+03 ... -3.661e+03 -3.66e+03
    latitudes        (y, x) float64 ...
    longitudes       (y, x) float64 ...
  * time             (time) datetime64[ns] 2016-05-29T13:59:59.999999936 ... ...
Data variables:
    rainfall_amount  (time, y, x) float32 ...
    maxrange         (time) int16 ...
    radarlocations   (time) object ...
    secondary        (time, y, x) float32 ...
    nodatamask       (time, y, x) float32 ...
    cluttermask      (time, y, x) float32 ...
    radolan_grid     float64 ...
Attributes:
    title:        RADOLAN YW rainfall data
    producttype:  YW
    institution:  Deutscher Wetterdienst (DWD)
    history:      Created at 2021-01-14 11:33:42.077117
    Conventions:  CF-1.6

# Plot 5-minute rainfall maps with time slider 

Note that I have not yet succeeded in adding a marker for the locations of Braunsbach in this plot. See the WIP version at the end of this notebook.

In [5]:
rainfall_map = ds.rainfall_amount.hvplot.quadmesh(
    x='longitudes', 
    y='latitudes',
    frame_width=500, 
    rasterize=True,
    tiles='OSM', 
    project=True, 
    geo=True, 
    clim=(0.1, 10), 
    cmap='rainbow', 
    clabel='rainfall amount (mm)')

rainfall_map.opts('Image', clipping_colors={'min': 'transparent', 'NaN': 'gray'}, alpha=0.5, toolbar='above')

rainfall_map

:DynamicMap   [time]
   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Image.I :Image   [longitudes,latitudes]   (rainfall_amount)

# Plot rainfall accumulation over the period covered by the data

Add coordinates of the village of Braunsbach as `pandas.Dataframe`, because this currently seems to be the easiest way to add a marker to the `hvplot` map.

In [6]:
import pandas as pd
import hvplot.pandas

braunsbach = pd.DataFrame(data={'x': [9.7913, ], 'y': [49.1992, ]})

In [7]:
print('First time stamp in data: ' + str(ds.rainfall_amount.time.values[0]))
print('Last time stamp in data : ' + str(ds.rainfall_amount.time.values[-1]))

First time stamp in data: 2016-05-29T13:59:59.999999936
Last time stamp in data : 2016-05-29T18:55:00.000000064


In [8]:
rainfall_map = ds.rainfall_amount.sum(dim='time').hvplot.quadmesh(
    x='longitudes', 
    y='latitudes',
    frame_width=500, 
    rasterize=True,
    tiles='OSM', 
    project=True, 
    geo=True, 
    clim=(0.1, 100), 
    cmap='rainbow', 
    clabel='rainfall amount (mm)')

rainfall_map.opts('Image', clipping_colors={'min': 'transparent', 'NaN': 'gray'}, alpha=0.5, toolbar='above')

rainfall_map * braunsbach.hvplot.points(x='x', y='y', geo=True, color='black')

:DynamicMap   []
   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Image.I  :Image   [longitudes,latitudes]   (rainfall_amount)
      .Points.I :Points   [x,y]

# [WIP] Rainfall map with time slider and marker for Braunsbach

Unfortunately the addition of `hvplot.points` to the map results in resizing the plot when the time slider is dragged. I did not yet find out how to solve this...

In [9]:
rainfall_map = ds.rainfall_amount.hvplot.quadmesh(
    x='longitudes', 
    y='latitudes',
    frame_width=500, 
    rasterize=True,
    tiles='OSM', 
    project=True, 
    geo=True, 
    clim=(0.1, 10), 
    cmap='rainbow', 
    clabel='rainfall amount (mm)')

rainfall_map.opts('Image', clipping_colors={'min': 'transparent', 'NaN': 'gray'}, alpha=0.5, toolbar='above')

rainfall_map * braunsbach.hvplot.points(x='x', y='y', geo=True, project=True, color='black')

:DynamicMap   [time]
   :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Image.I  :Image   [longitudes,latitudes]   (rainfall_amount)
      .Points.I :Points   [x,y]